In [1]:
# to set up logging
import logging
logging.basicConfig(format='%(asctime)s: %(levelname)s: %(message)s')
logging.root.setLevel(level=logging.INFO)

In [2]:
def get_p_description_html_from_sql(sql_database, sql_table):
    import mysql.connector
    
    sql_db = mysql.connector.connect(
        host = '127.0.0.1',
        user = 'root',
        password = '',
        database = sql_database
    )
    cursor = sql_db.cursor()
    
    # to check whether the TABLE is exist in the DATABASE
    cursor.execute("SHOW TABLES LIKE '{}'".format(sql_table))
    temp_result = cursor.fetchall()
    if(temp_result):
        logging.info("TABLE {} exists in DATABASE {}".format(sql_table, sql_database))
    else:
        logging.info("TABLE {} exists in DATABASE {}".format(sql_table, sql_database))
        
    #sql_select = "SELECT project_id, description_html FROM {}".format(sql_table)
    ################## IF THERE IS AN INTERRUPTION, EDIT HERE! ############################
    sql_select = "SELECT project_name, description_html FROM {} WHERE id > 3318".format(sql_table)
    cursor.execute(sql_select)
    p_description = cursor.fetchall()
    
    return p_description

# sql_database = 'practice_db'
# sql_table = 'v1_test_zeczec'
# p_description_html = get_p_description_html_from_sql(sql_database, sql_table)
# print(p_description_html[0])

In [3]:
def description_from_text(p_description_html):
    from bs4 import BeautifulSoup
    p_soup = BeautifulSoup(p_description_html, 'lxml')
    #print(p_soup.prettify())
    
    blacklist = [
        'script',
        'noscript',
        '[document]',
        'header',
        'html',
        'meta',
        'head',
        'input'
    ] # the element I don't want
    output = ''
    text = p_soup.find_all(text=True)
    
    #print(set([t.parent.name for t in text]))
    for t in text:
        if t.parent.name not in blacklist:
            output += '{}'.format(t)
    output = output.replace('\n', '').strip().replace(' ', '')
    
    return output

# output = description_from_text(temp_html)
# print(output)

In [4]:
def get_img_url_from_html(p_description_html):
    from bs4 import BeautifulSoup
    p_soup = BeautifulSoup(p_description_html, 'lxml')
    
    images = p_soup.find_all('img')
    img_urls = []

    for img in images:
        # to check img urls
        #logging.info(img)
        if img.has_attr('data-img-src'):
            img_url = img["data-img-src"]
            img_urls.append(img_url)
        if img.has_attr('src'):
            img_url = img["src"]
            img_urls.append(img_url)
            
#         else:
#             logging.info(img)
    
    return img_urls

# img_urls = get_img_url_from_html(temp_html)
# for img_url in img_urls:
#     print(img_url)

In [5]:
def detect_text_url(img_url):
    # to set up the environmental varuable: project key account
    # if need toe change project or account for the service, CHANGE HERE!!!
    import os
    #os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "My First Project-075ef2c4d2a4.json"
    os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "contentanalysis-0193c6e708c5.json"
    logging.info("os.environ: "+ os.environ["GOOGLE_APPLICATION_CREDENTIALS"])
    
    logging.info(img_url+" Extracting...")
    
    from google.cloud import vision
    client = vision.ImageAnnotatorClient() # to connect the service
    image = vision.Image() # toe create an Object Image
    image.source.image_uri = img_url # to import the image source by the url
    
    response = client.text_detection(image=image) # to pass the 'image' through 'client' for the text detetion
    texts = response.text_annotations # to get the texts from the result of 'response'
    
    logging.info(img_url+" Extracted")
    # if there is smoe problem of access the image, print error message and return False
    # else return the text extracted
    if (response.error.message):
        logging.info(response.error.message)
        return False
    else:
        if (texts): # if there are texts on the image
            for text in texts:
                return text.description
        else: # if there is no texts on the image
            return ""
# text = detect_text_url("https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292982_image_big.png?1616561650")
# print(text)

In [6]:
def download_image(folder_name, img_file_name, image_url):
    #from urllib.request import urlretrieve
    from pathlib import Path
    
    logging.info(image_url+" Downloading...")
    
    # to check whether folder exists or not
    folder_path = Path(folder_name)
    if (not(folder_path.exists())):
        folder_path.mkdir()
        logging.info("folder: "+folder_name+" Created")
    else:
        logging.info("folder: "+folder_name+" Existed")
        
    # to check whether the beginning is "data:image" or not
    temp_url = image_url.split('/')
    temp_url = temp_url[0]
    if (temp_url == 'data:image'):
        logging.info("{} can not be parse, pass result_text as blank string".format(image_url))
        return False
    else:
        # to check whether there is domain i nthe image_url
        check_domain = image_url.find("https:")
        flyingv_domain = "https://www.flyingv.cc"
        if (check_domain == -1): # If the value is not found, the find() method returns -1
            image_url = flyingv_domain+image_url

        # to add up the file type at the ned of the f_name
        if (image_url.find(".jpg") != -1):
            f_path = str(folder_path) + "\\" + img_file_name + ".jpg"
        elif (image_url.find(".gif") != -1):
            f_path = str(folder_path) + "\\" + img_file_name + ".gif"
        elif (image_url.find(".png") != -1):
            f_path = str(folder_path) + "\\" + img_file_name + ".png"
        else:
            logging.info("there is no type in image_url, add sub-title .jpg")
            f_path = str(folder_path) + "\\" + img_file_name + ".jpg"

        # to dowload and store the img through urlretrieve
        #urlretrieve(image_url, f_path)
        import requests as rq
        headers = {'User-Agent':'ozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/51.0.2704.103 Safari/537.36'}
        try:
            img_response = rq.get(image_url, headers=headers)
        except (rq.ConnectionError):
            logging.info("{} can not be accessed".format(image_url))
            return False
        else:
            img_file = open(f_path, "wb")
            img_file.write(img_response.content)
            img_file.close()
            logging.info(image_url+" Downloaded and saved as {} at {}".format(img_file_name, folder_name))

            return f_path

In [7]:
def detect_text_file (img_path):
    # to get the image file's name
    img_file_name = img_path.split('\\')
    img_file_name = img_file_name[-1]
    logging.info("image file {}".format(img_file_name)+" Extracting...")
    
    # to check whether there is content in the image first,
    # if there is no content, return false
    import cv2
    im = cv2.imread(img_path)
    if (im is None):
        logging.info("{} has no content, pass blank string back".format(img_file_name))
        return ""
    else:
        logging.info("{} has content to be extracted".format(img_file_name))
    
        # to set up the environmental varuable: project key account
        # if need toe change project or account for the service, CHANGE HERE!!!
        import os
        #os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "My First Project-075ef2c4d2a4.json"
        os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "contentanalysis-0193c6e708c5.json"
        logging.info("os.environ: "+ os.environ["GOOGLE_APPLICATION_CREDENTIALS"])

        from google.cloud import vision
        import io


        client = vision.ImageAnnotatorClient()
        with io.open(img_path, 'rb') as img_file:
            img_content = img_file.read()
        image = vision.Image(content=img_content)

        response = client.text_detection(image=image)
        texts = response.text_annotations

        if (response.error.message):
            logging.info("fail to get text from file {}, because {}".format(img_file_name, response.error.message))
            logging.info("return blank string for the pic")
            return ""
        else:
            logging.info("image file {}".format(img_file_name)+" Extracted")
            if (texts): # if there are texts on the image
                logging.info("hehe")
                for text in texts:
                    return text.description
            else: # if there is no texts on the image
                logging.info("ohoh")
                return ""
            
# folder_name = "temp_image_zec"
# img_url = "https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_293899_image_big.png?1616673175"
# file_path = download_image(folder_name, "test_01", img_url)
# print(file_path)
# output = detect_text_file(file_path)
# print(output)

In [8]:
def insert_p_description_into_mysql(sql_database, sql_table, p_name, p_description):
    import mysql.connector
    
    sql_db = mysql.connector.connect(
        host = "127.0.0.1",
        user = "root",
        password="",
        database = sql_database
    )
    
    # to check whether the TABLE exists or not
    cursor = sql_db.cursor()
    cursor.execute("SHOW TABLES LIKE '{}'".format(sql_table))
    temp_result = cursor.fetchone()
    if (temp_result):
        logging.info("TABLE {} exists in DATABASE {}".format(sql_table, sql_database))
    else:
        logging.info("No TABLE {} in DATABASE {}".format(sql_table, sql_database))
        
    # to UPDATE description_text, WHERE p_name
    logging.info("project {} started to INSERT".format(p_name))
    sql_update = "UPDATE {} SET description_text='{}' WHERE project_name='{}'".format(sql_table, p_description, p_name)
    cursor.execute(sql_update)
    sql_db.commit()
    logging.info("project {} INESRTED in TABLE {}".format(p_name, sql_table))
# sql_database = 'practice_db'
# sql_table = 'v1_test_zeczec'
# p_name = 'perzon-buds-anc'
# p_description = "test"
# insert_p_description_into_mysql(sql_database, sql_table, p_name, p_description)
                                                                                

In [9]:
def main():
    # to set logging
    import logging
    logging.basicConfig(format='%(asctime)s: %(levelname)s: %(message)s')
    logging.root.setLevel(level=logging.INFO)
    
    ################### CHANGE DATABASE HERE ##########################
    sql_database = 'crowdfunding_db'
    sql_table = 'v3_latest_zeczec_basic_project_information'
    p_description_html = get_p_description_html_from_sql(sql_database, sql_table)
    p_count = 1
    for p in p_description_html:
        p_name = p[0]
        p_description_html = p[1]
        
        description_text = description_from_text(p_description_html)
        # to show the description from text
        #logging.info(p_name)+": "+description_text)
        
        description_img = ''
        img_urls = get_img_url_from_html(p_description_html)

        # to extract text from each image for the project
        img_count = 1 # for number the name of the jpg file
        logging.info("the number of the imgs in {} is {}".format(p_name, str(len(img_urls))))
        for img_url in img_urls:
            # to extract text from image online
            result_text = detect_text_url(img_url)
            # if there is result_text, gather it to description_img
            # else download the img and extract the text
            if (result_text):
                result_text.strip()
                description_img += result_text
            else: # extract text from image locally
                # to download the image
                folder_name = "temp_image_zec"
                img_file_name = p_name+"_"+str(img_count)
                f_path = download_image(folder_name, img_file_name, img_url)
                # if the img_url can not accessed
                if (f_path):
                    result_text = detect_text_file(f_path)
                else:
                    logging.info("{} can not be downloaded, assign the result_text blank string".format(img_url))
                    result_text = ""
                logging.info("result_text: "+result_text)
                result_text.strip()
                description_img += result_text
            logging.info(img_url+" extract text DONE")
            img_count += 1

            ############## TEST img EXTRACTED HERE#################
#             if (img_count == 10):
#                 break
#         if (p_count == 5):
#             break
                    
        project_total_description = description_text + description_img
        project_total_description = project_total_description.replace("'", "")
        # to show the description from text_pic
        logging.info("project {} description: {}".format(p_name, project_total_description))
        insert_p_description_into_mysql(sql_database, sql_table, p_name, project_total_description)
        logging.info("project {} DONE".format(p_name))
        p_count += 1
        
    logging.info("zeczec project description extracting DONE")

In [10]:
if __name__ == "__main__":
    main()

2021-05-03 10:53:07,559: INFO: TABLE v3_latest_zeczec_basic_project_information exists in DATABASE crowdfunding_db
2021-05-03 10:53:07,784: INFO: the number of the imgs in mplus is 20
2021-05-03 10:53:07,785: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:53:07,787: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_34810_image_big.png Extracting...
2021-05-03 10:53:10,879: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_34810_image_big.png Extracted
2021-05-03 10:53:10,886: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_34810_image_big.png Downloading...
2021-05-03 10:53:10,888: INFO: folder: temp_image_zec Existed
2021-05-03 10:53:11,256: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_34810_image_big.png Downloaded and saved as mplus_1 at temp_image_zec
2021-05-03 10:53:11,258: INFO: image file mplus_1.png Extracting...
2021-05-03 10:53:11,470: INFO: mplus_1.png has content to be extracted
2021-05-03 10

2021-05-03 10:53:46,559: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:53:46,560: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75986_image_big.jpg?1545627677 Extracting...
2021-05-03 10:53:47,873: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75986_image_big.jpg?1545627677 Extracted
2021-05-03 10:53:47,878: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75986_image_big.jpg?1545627677 extract text DONE
2021-05-03 10:53:47,879: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:53:47,881: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75993_image_big.jpg?1545628274 Extracting...
2021-05-03 10:53:50,186: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75993_image_big.jpg?1545628274 Extracted
2021-05-03 10:53:50,191: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_75993_image_big.jpg?1545628274 extract text DONE
2021-05-03 10:53:50,192: INFO: os.environ:

2021-05-03 10:54:07,233: INFO: TABLE v3_latest_zeczec_basic_project_information exists in DATABASE crowdfunding_db
2021-05-03 10:54:07,234: INFO: project mplus started to INSERT
2021-05-03 10:54:07,422: INFO: project mplus INESRTED in TABLE v3_latest_zeczec_basic_project_information
2021-05-03 10:54:07,424: INFO: project mplus DONE
2021-05-03 10:54:07,455: INFO: the number of the imgs in lettherebelighttw is 13
2021-05-03 10:54:07,456: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:54:07,457: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_37587_image_big.jpg?1516520704 Extracting...
2021-05-03 10:54:09,372: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_37587_image_big.jpg?1516520704 Extracted
2021-05-03 10:54:09,379: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_37587_image_big.jpg?1516520704 extract text DONE
2021-05-03 10:54:09,380: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:54:09,381: INFO

2021-05-03 10:54:35,766: INFO: TABLE v3_latest_zeczec_basic_project_information exists in DATABASE crowdfunding_db
2021-05-03 10:54:35,767: INFO: project lettherebelighttw started to INSERT
2021-05-03 10:54:35,953: INFO: project lettherebelighttw INESRTED in TABLE v3_latest_zeczec_basic_project_information
2021-05-03 10:54:35,956: INFO: project lettherebelighttw DONE
2021-05-03 10:54:36,070: INFO: the number of the imgs in mondayschool is 19
2021-05-03 10:54:36,071: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:54:36,072: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43303_image_big.png?1522396384 Extracting...
2021-05-03 10:54:39,572: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43303_image_big.png?1522396384 Extracted
2021-05-03 10:54:39,576: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43303_image_big.png?1522396384 extract text DONE
2021-05-03 10:54:39,578: INFO: os.environ: contentanalysis-0193c6e708c5.jso

2021-05-03 10:55:04,495: INFO: ohoh
2021-05-03 10:55:04,500: INFO: result_text: 
2021-05-03 10:55:04,502: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_38867_image_big.jpg?1517957853 extract text DONE
2021-05-03 10:55:04,503: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 10:55:04,504: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43327_image_big.png?1522402621 Extracting...
2021-05-03 10:55:05,740: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43327_image_big.png?1522402621 Extracted
2021-05-03 10:55:05,744: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43327_image_big.png?1522402621 Downloading...
2021-05-03 10:55:05,746: INFO: folder: temp_image_zec Existed
2021-05-03 10:55:06,169: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_43327_image_big.png?1522402621 Downloaded and saved as mondayschool_13 at temp_image_zec
2021-05-03 10:55:06,171: INFO: image file mondayschool_13.png Ext

...

2021-05-03 15:41:55,744: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:41:55,744: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292994_image_big.jpg?1616562978 Extracting...
2021-05-03 15:41:56,690: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292994_image_big.jpg?1616562978 Extracted
2021-05-03 15:41:56,694: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292994_image_big.jpg?1616562978 extract text DONE
2021-05-03 15:41:56,695: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:41:56,696: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292995_image_big.jpg?1616563135 Extracting...
2021-05-03 15:41:57,643: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292995_image_big.jpg?1616563135 Extracted
2021-05-03 15:41:57,648: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292995_image_big.jpg?1616563135 extract text DONE
2021-05-03 15:41:57,649: INFO: os.en

2021-05-03 15:42:09,472: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_284915_image_big.gif?1614674017 extract text DONE
2021-05-03 15:42:09,473: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:42:09,474: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_291587_image_big.png?1616234394 Extracting...
2021-05-03 15:42:11,426: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_291587_image_big.png?1616234394 Extracted
2021-05-03 15:42:11,430: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_291587_image_big.png?1616234394 extract text DONE
2021-05-03 15:42:11,431: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:42:11,432: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_284942_image_big.gif?1614674828 Extracting...
2021-05-03 15:42:13,211: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_284942_image_big.gif?1614674828 Extracted
2021-05-03 15:42:13,215: INFO: https

2021-05-03 15:42:46,702: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_294266_image_big.png?1616742507 extract text DONE
2021-05-03 15:42:46,703: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:42:46,705: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292989_image_big.png?1616562212 Extracting...
2021-05-03 15:42:48,548: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292989_image_big.png?1616562212 Extracted
2021-05-03 15:42:48,554: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292989_image_big.png?1616562212 extract text DONE
2021-05-03 15:42:48,556: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:42:48,557: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292554_image_big.png?1616483779 Extracting...
2021-05-03 15:42:50,382: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_292554_image_big.png?1616483779 Extracted
2021-05-03 15:42:50,386: INFO: https

2021-05-03 15:43:15,061: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_287624_image_big.gif?1615303903 Extracted
2021-05-03 15:43:15,067: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_287624_image_big.gif?1615303903 Downloading...
2021-05-03 15:43:15,069: INFO: folder: temp_image_zec Existed
2021-05-03 15:43:15,567: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_287624_image_big.gif?1615303903 Downloaded and saved as drinkhaha_9 at temp_image_zec
2021-05-03 15:43:15,569: INFO: image file drinkhaha_9.gif Extracting...
2021-05-03 15:43:15,572: INFO: drinkhaha_9.gif has no content, pass blank string back
2021-05-03 15:43:15,573: INFO: result_text: 
2021-05-03 15:43:15,574: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_287624_image_big.gif?1615303903 extract text DONE
2021-05-03 15:43:15,575: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:43:15,575: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec

2021-05-03 15:43:53,390: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288005_image_big.png?1615388778 Extracted
2021-05-03 15:43:53,394: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288005_image_big.png?1615388778 extract text DONE
2021-05-03 15:43:53,395: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:43:53,396: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288007_image_big.png?1615388802 Extracting...
2021-05-03 15:43:55,338: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288007_image_big.png?1615388802 Extracted
2021-05-03 15:43:55,343: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288007_image_big.png?1615388802 extract text DONE
2021-05-03 15:43:55,344: INFO: os.environ: contentanalysis-0193c6e708c5.json
2021-05-03 15:43:55,345: INFO: https://s3-ap-northeast-1.amazonaws.com/zeczec-prod/asset_288008_image_big.png?1615388826 Extracting...
2021-05-03 15:43:57,862: INFO: https